# Hololive

In [ ]:
#!pwsh
$BaseUrl = "http://10.16.1.100:8016/odata/HololiveSchedule"
$TimeoutSec = 10
$ArchiveDir = "/mnt/hdd/hololive-archive"

try {
    $JstTz = [TimeZoneInfo]::FindSystemTimeZoneById("Tokyo Standard Time")
} catch {
    $JstTz = [TimeZoneInfo]::FindSystemTimeZoneById("Asia/Tokyo")
}

$nowJst = [TimeZoneInfo]::ConvertTime([DateTimeOffset]::Now, $JstTz)
$today = $nowJst.Date
$yesterdayEndLocal = $today.AddDays(-1).AddHours(23).AddMinutes(59).AddSeconds(59)
$yesterdayEnd = [DateTimeOffset]::new($yesterdayEndLocal, $JstTz.GetUtcOffset($yesterdayEndLocal))

$params = @{
    '$filter' = "StartDt le $($yesterdayEnd.ToString('o'))"
    '$select' = "Id,StartDt,MemberName,StreamUrl,StreamTitle,StreamImage,Md5"
}

function Get-QueryString($p) {
    if (-not $p) { return "" }
    ($p.GetEnumerator() | ForEach-Object {
        "{0}={1}" -f [uri]::EscapeDataString($_.Key), [uri]::EscapeDataString($_.Value)
    }) -join "&"
}

$rows = @()
$url = $BaseUrl

while ($true) {
    $reqUrl = $url
    $qs = Get-QueryString $params
    if ($qs) {
        $reqUrl = "$url`?$qs"
    }

    $data = Invoke-RestMethod -Uri $reqUrl -Method Get -TimeoutSec $TimeoutSec
    if ($null -ne $data.value) {
        $rows += $data.value
    }
    $url = $data.'@odata.nextLink'
    $params = $null
    if (-not $url) { break }
}

if (-not $rows -or $rows.Count -eq 0) {
    Write-Host "没找到需要归档的数据"
} else {
    $byMonth = @{}
    foreach ($r in $rows) {
        $dtObj = [TimeZoneInfo]::ConvertTime([DateTimeOffset]::Parse($r.StartDt), $JstTz)
        $ym = $dtObj.ToString("yyyy-MM")
        if (-not $byMonth.ContainsKey($ym)) { $byMonth[$ym] = @() }
        $byMonth[$ym] += $r
    }

    foreach ($ym in $byMonth.Keys) {
        $items = $byMonth[$ym]
        $path = Join-Path $ArchiveDir "$ym.csv"

        $existing = @{}
        if (Test-Path $path) {
            Import-Csv -Path $path | ForEach-Object {
                $existing[$_.Md5] = $_
            }
        }

        foreach ($r in $items) {
            $existing[$r.Md5] = [pscustomobject]@{
                StartDt = $r.StartDt
                MemberName = $r.MemberName
                StreamUrl = $r.StreamUrl
                StreamTitle = $r.StreamTitle
                StreamImage = $(if ($null -eq $r.StreamImage) { "" } else { $r.StreamImage })
                Md5 = $r.Md5
            }
        }

        $existing.Values | Sort-Object StartDt | Export-Csv -Path $path -NoTypeInformation -Encoding UTF8
        Write-Host "ARCHIVED $ym.csv : $($items.Count) 条"
    }

    foreach ($r in $rows) {
        $deleteUrl = "$BaseUrl($($r.Id))"
        Invoke-RestMethod -Uri $deleteUrl -Method Delete -TimeoutSec $TimeoutSec | Out-Null
        Write-Host "DELETE $($r.StartDt) | $($r.StreamTitle)"
    }

    Write-Host "完成，归档并删除 $($rows.Count) 条"
}
